In [1]:
import folium as fm
import pandas as pd
import numpy as np
import geopandas as gpd
from shapely.geometry import Point, Polygon
from fiona.drvsupport import supported_drivers
import panel as pn
from fastkml.kml import KML
import matplotlib.pyplot as plt
pn.extension(sizing_mode="stretch_width")

1. Read file into memory

In [19]:
#these first blocks are just so you guys can see what I did to get the zipcode layer built
#kml downloaded from https://www2.census.gov/geo/tiger/GENZ2020/kml/cb_2020_us_zcta520_500k.zip
#I didn't commit the full file because it is too big for github
supported_drivers['KML'] = 'rw'
zip_geography = gpd.read_file('./cb_2020_us_zcta520_500k.kml', driver='KML')

In [14]:
zip_geography.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 33791 entries, 0 to 33790
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype   
---  ------       --------------  -----   
 0   Name         33791 non-null  object  
 1   Description  33791 non-null  object  
 2   geometry     33791 non-null  geometry
dtypes: geometry(1), object(2)
memory usage: 792.1+ KB


In [2]:
#reads state boundries for the US so that I can filter out just DC, MD, and VA zips.
supported_drivers['KML'] = 'rw'
state_geography = gpd.read_file('./cb_2020_us_state_500k.kml', driver='KML')

In [3]:
dc_places = gpd.read_file('./cb_2020_11_place_500k.kml', driver='KML')

Name  \
0                  <at><openparen>Alabama<closeparen>   
1                   <at><openparen>Alaska<closeparen>   
2           <at><openparen>American Samoa<closeparen>   
3                  <at><openparen>Arizona<closeparen>   
4                 <at><openparen>Arkansas<closeparen>   
5               <at><openparen>California<closeparen>   
6                 <at><openparen>Colorado<closeparen>   
7   <at><openparen>Commonwealth of the Northern Ma...   
8              <at><openparen>Connecticut<closeparen>   
9                 <at><openparen>Delaware<closeparen>   
10    <at><openparen>District of Columbia<closeparen>   
11                 <at><openparen>Florida<closeparen>   
12                 <at><openparen>Georgia<closeparen>   
13                    <at><openparen>Guam<closeparen>   
14                  <at><openparen>Hawaii<closeparen>   
15                   <at><openparen>Idaho<closeparen>   
16                <at><openparen>Illinois<closeparen>   
17                 <at><openparen>Indiana<closeparen>   
18                    <at><openparen>Iowa<closeparen>   
19                  <at><openparen>Kansas<closeparen>   
20                <at><openparen>Kentucky<closeparen>   
21               <at><openparen>Louisiana<closeparen>   
22                   <at><openparen>Maine<closeparen>   
23                <at><openparen>Maryland<closeparen>   
24           <at><openparen>Massachusetts<closeparen>   
25                <at><openparen>Michigan<closeparen>   
26               <at><openparen>Minnesota<closeparen>   
27             <at><openparen>Mississippi<closeparen>   
28                <at><openparen>Missouri<closeparen>   
29                 <at><openparen>Montana<closeparen>   
30                <at><openparen>Nebraska<closeparen>   
31                  <at><openparen>Nevada<closeparen>   
32           <at><openparen>New Hampshire<closeparen>   
33              <at><openparen>New Jersey<closeparen>   
34              <at><openparen>New Mexico<closeparen>   
35                <at><openparen>New York<closeparen>   
36          <at><openparen>North Carolina<closeparen>   
37            <at><openparen>North Dakota<closeparen>   
38                    <at><openparen>Ohio<closeparen>   
39                <at><openparen>Oklahoma<closeparen>   
40                  <at><openparen>Oregon<closeparen>   
41            <at><openparen>Pennsylvania<closeparen>   
42             <at><openparen>Puerto Rico<closeparen>   
43            <at><openparen>Rhode Island<closeparen>   
44          <at><openparen>South Carolina<closeparen>   
45            <at><openparen>South Dakota<closeparen>   
46               <at><openparen>Tennessee<closeparen>   
47                   <at><openparen>Texas<closeparen>   
48  <at><openparen>United States Virgin Islands<cl...   
49                    <at><openparen>Utah<closeparen>   
50                 <at><openparen>Vermont<closeparen>   
51                <at><openparen>Virginia<closeparen>   
52              <at><openparen>Washington<closeparen>   
53           <at><openparen>West Virginia<closeparen>   
54               <at><openparen>Wisconsin<closeparen>   
55                 <at><openparen>Wyoming<closeparen>   

                                          Description  \
0   <center><table><tr><th colspan='2' align='cent...   
1   <center><table><tr><th colspan='2' align='cent...   
2   <center><table><tr><th colspan='2' align='cent...   
3   <center><table><tr><th colspan='2' align='cent...   
4   <center><table><tr><th colspan='2' align='cent...   
5   <center><table><tr><th colspan='2' align='cent...   
6   <center><table><tr><th colspan='2' align='cent...   
7   <center><table><tr><th colspan='2' align='cent...   
8   <center><table><tr><th colspan='2' align='cent...   
9   <center><table><tr><th colspan='2' align='cent...   
10  <center><table><tr><th colspan='2' align='cent...   
11  <center><table><tr><th colspan='2' align='cent...   
12  <center><table><tr><th colspan='2' align='cent...   
1

Chris Smith, replicate the above read in for the three 'places' kml files and concat like below to produce your geodataframe that you will add your metric series column to.

In [4]:
project_zips = gpd.GeoDataFrame()
dc_zips = zip_geography[zip_geography.geometry.within(state_geography.loc[10].geometry)]
md_zips = zip_geography[zip_geography.geometry.within(state_geography.loc[23].geometry)]
va_zips = zip_geography[zip_geography.geometry.within(state_geography.loc[51].geometry)]
project_zips = pd.concat([dc_zips, md_zips, va_zips])
project_zips.to_file('DC_MD_VA_Zipcodes.kml', driver = 'KML') #saves df to kml file

NameError: name 'zip_geography' is not defined

In [50]:
supported_drivers['KML'] = 'rw'
project_zips = gpd.read_file('./DC_MD_VA_Zipcodes.kml', driver='KML')

In [53]:
project_zips.head()

Name  \
0  <at><openparen>20001<closeparen>   
1  <at><openparen>20002<closeparen>   
2  <at><openparen>20003<closeparen>   
3  <at><openparen>20004<closeparen>   
4  <at><openparen>20005<closeparen>   

                                         Description  \
0  <center><table><tr><th colspan='2' align='cent...   
1  <center><table><tr><th colspan='2' align='cent...   
2  <center><table><tr><th colspan='2' align='cent...   
3  <center><table><tr><th colspan='2' align='cent...   
4  <center><table><tr><th colspan='2' align='cent...   

                                            geometry  
0  POLYGON Z ((-77.02758 38.90964 0.00000, -77.02...  
1  POLYGON Z ((-77.01217 38.89209 0.00000, -77.01...  
2  POLYGON Z ((-77.01402 38.88236 0.00000, -77.01...  
3  POLYGON Z ((-77.03365 38.89735 0.00000, -77.03...  
4  POLYGON Z ((-77.03654 38.90252 0.00000, -77.03...

You need to add a series column to the above geodataframe that has the associated value for your metric for each zipcode geography. (if using zip codes as your map layer area boundry.

In [51]:
#Point takes long then lat
pentagon = (38.8719570149196, -77.05630981703996)
pentagon_grid = Point(pentagon[1],pentagon[0])

In [52]:
#Once you have your metric loaded on your GeoDataFrame above, you can use the code below to start 
#to visualize. We will work more on the fillcolor and popups later.
zip_map = fm.Map(location=pentagon, zoom_start=12, tiles='CartoDB positron')
fm.Marker(pentagon, popup = 'Pentagon').add_to(zip_map)
for _, r in project_zips.iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = fm.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    fm.Popup(r['Description']).add_to(geo_j)
    geo_j.add_to(zip_map)
zip_map